In [ ]:
# Learning Practice 9 for the University of Tulsa's QM-7063 Data Mining Course
# Support Vector Machines
# Professor: Dr. Abdulrashid, Spring 2023
# Noah L. Schrick - 1492657

In [28]:
# Imports
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import classification_report,confusion_matrix

%matplotlib inline

# a. 
Numerisize the dataset

In [17]:
# a
accidents_df = pd.read_csv('accidentsFull.csv')
accidents_df['Injury'] = (accidents_df['MAX_SEV_IR'] > 0).astype(int)
accidents_df = accidents_df.apply(pd.to_numeric) # convert all columns of DataFrame


# b. 
Transform the data by either normalizing or standardizing it.

In [18]:
# b. and c.
scaler = preprocessing.StandardScaler()

accident_cols = accidents_df.columns.values.tolist()
accident_cols.remove('Injury')

# split into training and validation
trainData, validData = train_test_split(accidents_df, test_size=0.40, random_state=20)

scaler.fit(trainData[accident_cols])  # Note the use of an array of column names

# Transform the full dataset
accidentNorm = pd.concat([pd.DataFrame(scaler.transform(accidents_df[accident_cols]), 
                                    columns=accident_cols),
                        accidents_df[['Injury']]], axis=1)

trainNorm = accidentNorm.iloc[trainData.index]
validNorm = accidentNorm.iloc[validData.index]

# c. 
Use train, test, and split function to split the data into training and testing sets.

In [21]:
# c. 
train_X = trainNorm[accident_cols]
train_y = trainNorm['Injury']
valid_X = validNorm[accident_cols]
valid_y = validNorm['Injury']

# d.
Select your preferred kernel type and determine the kernel values by using either grid-search or v-fold cross validation.

In [29]:
# d.
param_grid = {'C': [0.1,1, 10, 100, 1000], 'gamma': [1,0.1,0.01,0.001,0.0001], 'kernel': ['rbf']} 
grid = GridSearchCV(SVC(),param_grid,refit=True,verbose=3)
grid.fit(train_X,train_y)


Fitting 5 folds for each of 25 candidates, totalling 125 fits
[CV 1/5] END ........C=0.1, gamma=1, kernel=rbf;, score=0.772 total time=  33.9s
[CV 2/5] END ........C=0.1, gamma=1, kernel=rbf;, score=0.762 total time=  46.2s
[CV 3/5] END ........C=0.1, gamma=1, kernel=rbf;, score=0.769 total time=  42.3s
[CV 4/5] END ........C=0.1, gamma=1, kernel=rbf;, score=0.762 total time=  36.2s
[CV 5/5] END ........C=0.1, gamma=1, kernel=rbf;, score=0.761 total time=  34.8s
[CV 1/5] END ......C=0.1, gamma=0.1, kernel=rbf;, score=0.999 total time=   5.6s
[CV 2/5] END ......C=0.1, gamma=0.1, kernel=rbf;, score=0.996 total time=   5.8s
[CV 3/5] END ......C=0.1, gamma=0.1, kernel=rbf;, score=0.998 total time=   5.6s
[CV 4/5] END ......C=0.1, gamma=0.1, kernel=rbf;, score=0.995 total time=   5.6s
[CV 5/5] END ......C=0.1, gamma=0.1, kernel=rbf;, score=0.997 total time=   5.7s
[CV 1/5] END .....C=0.1, gamma=0.01, kernel=rbf;, score=1.000 total time=   1.1s
[CV 2/5] END .....C=0.1, gamma=0.01, kernel=rbf

GridSearchCV(estimator=SVC(),
             param_grid={'C': [0.1, 1, 10, 100, 1000],
                         'gamma': [1, 0.1, 0.01, 0.001, 0.0001],
                         'kernel': ['rbf']},
             verbose=3)

In [38]:
# Best options:
grid.best_params_
print()
grid.best_estimator_

SVC(C=0.1, gamma=0.001)

# e.
Run a SVM classifier using identified kernel values found in (d).

In [42]:
# e.
grid_predictions = grid.predict(valid_X)

# f.
Obtain the confusion matrix.

In [43]:
# f. 
print(confusion_matrix(valid_y,grid_predictions))

[[8270    0]
 [   0 8604]]


# g.
What is the overall error for the validation set?

In [44]:
# g. 
print(classification_report(valid_y,grid_predictions))

              precision    recall  f1-score   support

           0       1.00      1.00      1.00      8270
           1       1.00      1.00      1.00      8604

    accuracy                           1.00     16874
   macro avg       1.00      1.00      1.00     16874
weighted avg       1.00      1.00      1.00     16874

